<a href="https://colab.research.google.com/github/aditya-007/AGE-work/blob/main/Dispatch_optimization_2023_Italy.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Battery dispatch optimization
The goal of this exercise is to optimize the charge/discharge behavior of a battery system performing energy arbitrage in the Italian market. The model objective is to maximize profit over a year and the project objective is to gain insights into market dynamics and expected system behavior. We have hourly electricity price data for the entire year (taken from ENTSO-E for 2023), which we assume is accurate with perfect foresight.

The battery system has maximum storage capacity of 30 MWh and a power rating of 15 MW (charge and discharge). Round-trip AC-AC efficiency is 85%. The maximum daily discharge throughput is constrained to 30 MWh within a 24-hour period.

In [ ]:
pip install -r requirements.txt

ERROR: Could not find a version that satisfies the requirement nb_conda_kernels (from versions: none)
ERROR: No matching distribution found for nb_conda_kernels


In [ ]:
!pip install -q pyomo

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 39.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 2.4 MB/s eta 0:00:00


In [ ]:
!apt-get install -y -qq glpk-utils

Selecting previously unselected package libsuitesparseconfig5:amd64.
(Reading database ... 123599 files and directories currently installed.)
Preparing to unpack .../libsuitesparseconfig5_1%3a5.10.1+dfsg-4build1_amd64.deb ...
Unpacking libsuitesparseconfig5:amd64 (1:5.10.1+dfsg-4build1) ...
Selecting previously unselected package libamd2:amd64.
Preparing to unpack .../libamd2_1%3a5.10.1+dfsg-4build1_amd64.deb ...
Unpacking libamd2:amd64 (1:5.10.1+dfsg-4build1) ...
Selecting previously unselected package libcolamd2:amd64.
Preparing to unpack .../libcolamd2_1%3a5.10.1+dfsg-4build1_amd64.deb ...
Unpacking libcolamd2:amd64 (1:5.10.1+dfsg-4build1) ...
Selecting previously unselected package libglpk40:amd64.
Preparing to unpack .../libglpk40_5.0-1_amd64.deb ...
Unpacking libglpk40:amd64 (5.0-1) ...
Selecting previously unselected package glpk-utils.
Preparing to unpack .../glpk-utils_5.0-1_amd64.deb ...
Unpacking glpk-utils (5.0-1) ...
Setting up libsuitesparseconfig5:amd64 (1:5.10.1+dfsg-4b

In [ ]:
import pandas as pd
from pathlib import Path
import altair as alt

In [ ]:
def read_excel_to_df(path):
    """
    Read an Excel file with pandas and store the data in a DataFrame.

    Parameters
    ----------
    path : str or other object for read_excel filepath parameter
        Path to Excel file with data

    Returns
    -------
    DataFrame
        df with data from the Excel file
    """

    df = pd.read_excel(path)
    return df

In [ ]:
import numpy as np
from pyomo.environ import *

In [ ]:
from datetime import datetime, timedelta

In [ ]:
def model_to_df(model, first_hour, last_hour, start_time='2023-01-01 00:00:00'):
    """
    Create a dataframe with hourly charge, discharge, state of charge, and
    price columns from a pyomo model. Only uses data from between the first
    (inclusive) and last (exclusive) hours.

    Parameters
    ----------
    model : pyomo model
        Model that has been solved

    first_hour : int
        First hour of data to keep
    last_hour: int
        The final hour of data to keep

    Returns
    -------
    dataframe

    """
    # Need to increase the first & last hour by 1 because of pyomo indexing
    # and add 1 to the value of last model hour because of the range
    # second model hour by 1
    hours = range(model.T[first_hour+1], model.T[last_hour+1]+1)
    Ein = [value(model.Ein[i]) for i in hours]
    Eout = [value(model.Eout[i]) for i in hours]
    price = [model.P.extract_values()[None][i] for i in hours]
    #output = [model.O.extract_values()[None][i] for i in hours]
    #output = [model.O[i] for i in hours]
    charge_state = [value(model.S[i]) for i in hours]

    # Generate timestamps
    start_datetime = datetime.strptime(start_time, '%Y-%m-%d %H:%M:%S')
    timestamps = [start_datetime + timedelta(hours=i) for i in hours]

    df_dict = dict(
        hour=hours,
        timestamp=timestamps,
        Ein=Ein,
        Eout=Eout,
        price=price,
        #output=output,
        charge_state=charge_state
    )

    df = pd.DataFrame(df_dict)

    return df

In [ ]:
def optimize_year(df, first_model_hour=0, last_model_hour=8759):
    """
    Optimize the charge/discharge behavior of a battery storage unit over a
    full year. Assume perfect foresight of electricity prices. The battery
    has a discharge constraint equal to its storage capacity and round-trip
    efficiency of 85%.

    Parameters
    ----------
    df : dataframe
        dataframe with columns of hourly price and the hour of the year
    first_model_hour : int, optional
        Set the first hour of the year to be considered in the optimization
        (the default is 0)
    last_model_hour : int, optional
        Set the last hour of the year to be considered in the optimization (the
        default is 8759)

    Returns
    -------
    dataframe
        hourly state of charge, charge/discharge behavior, lbmp, and time stamp
    """

    #Filter the data
    df = df.loc[first_model_hour:last_model_hour, :]

    model = ConcreteModel()

    # Define model parameters
    model.T = Set(doc='hour of year', initialize=df.Hour.tolist(), ordered=True)
    model.Rmax = Param(initialize=15,
                       doc='Max rate of power flow (MW) in or out')
    model.Smax = Param(initialize=24, doc='Max storage (kWh)')
    model.Dmax = Param(initialize=24, doc='Max discharge in 24 hour period')
    model.P = Param(initialize=df.Price.tolist(), doc='Price for each hour')
    #model.O = Param(model.T, initialize=df.Power.tolist(), doc='Output of the plant (MW)')
    eta = 0.85 # Round trip storage efficiency

    # Charge, discharge, and state of charge
    # Could use bounds for the first 2 instead of constraints
    model.Ein = Var(model.T, domain=NonNegativeReals)
    model.Eout = Var(model.T, domain=NonNegativeReals)
    model.S = Var(model.T, bounds=(0, model.Smax))


    #Set all constraints
    def storage_state(model, t):
        'Storage changes with flows in/out and efficiency losses'
        # Set first hour state of charge to half of max
        if t == model.T.first():
            return model.S[t] == model.Smax / 2
        else:
            return (model.S[t] == (model.S[t-1]
                                + (model.Ein[t-1] * np.sqrt(eta))
                                - (model.Eout[t-1] / np.sqrt(eta))))

    model.charge_state = Constraint(model.T, rule=storage_state)

    def discharge_constraint(model, t):
        "Maximum dischage within a single hour"
        return model.Eout[t] <= model.Rmax

    model.discharge = Constraint(model.T, rule=discharge_constraint)

    def charge_constraint(model, t):
        "Maximum charge within a single hour"
        #out = model.O[t]
        return model.Ein[t] <= model.Rmax

    model.charge = Constraint(model.T, rule=charge_constraint)

    # Without a constraint the model would discharge in the final hour
    # even when SOC was 0.
    def positive_charge(model, t):
        'Limit discharge to the amount of charge in battery, including losses'
        return model.Eout[t] <= model.S[t] / np.sqrt(eta)
    model.positive_charge = Constraint(model.T, rule=positive_charge)

    def discharge_limit(model, t):
        "Limit on discharge within a 24 hour period"
        max_t = model.T.last()

        # Check all t until the last 24 hours
        # No need to check with < 24 hours remaining because the constraint is
        # already in place for a larger number of hours
        if t < max_t - 24:
            return sum(model.Eout[i] for i in range(t, t+24)) <= model.Dmax
        else:
            return Constraint.Skip

    model.limit_out = Constraint(model.T, rule=discharge_limit)

    # Define the battery income, expenses, and profit
    income = sum(df.loc[t, 'Price'] * model.Eout[t] for t in model.T)
    expenses = sum(df.loc[t, 'Price'] * model.Ein[t] for t in model.T)
    profit = income - expenses
    model.objective = Objective(expr=profit, sense=maximize)

    # Solve the model
    solver = SolverFactory("glpk",executable='/usr/bin/glpsol')
    solver.solve(model)

    results_df = model_to_df(model, first_hour=first_model_hour,
                             last_hour=last_model_hour)

    return results_df

In [ ]:

# Select your appropriate notebook type for rendering Altair figures
alt.renderers.enable('jupyterlab')
# alt.renderers.enable('notebook')
alt.data_transformers.enable('default', max_rows=None)


DataTransformerRegistry.enable('default')

## Read data
Functions to read data and run the optimization model are provided in scripts in the `src` folder.

In [ ]:
data_path = 'ElectricityPriceItaly2023.xlsx'

df = read_excel_to_df(data_path)

In [ ]:
df.head()

Hour   Price
0     0  195.90
1     1  191.09
2     2  187.95
3     3  187.82
4     4  187.74

## Model parameters and constraints

**Parameters**
- $t$: timestep or hour
- $R_{max}$ (100 kW): maximum power than can be delivered to or from the battery (charge or discharge rate)
- $S_{max}$ (200 kWh): maximum battery capacity
- $S_t$: storage at time $t$
- Eff ($\eta$) (85%): efficiency
- $D_{max}$ (200 kWh): max discharge within a 24 hour period
- $P_t$: LBMP at time $t$

**Decision variables**
- $E^{in}_t$: energy delivered to the battery at time $t$
- $E^{out}_t$: energy discharged from the battery at time $t$

**Constraints**
- $S_1$ = $\frac{S_{max}}{2}$ (Assume storage begins at half of capacity)
- $S_t$ = $S_{t-1} + \sqrt{\eta} \times E^{in}_{t-1} - \frac{E^{out}_{t-1}}{\sqrt{\eta}}$
- $\forall t, S_t \geq 0$
- $\forall t, S_t \leq S_{max}$
- $\forall t, E^{in}_t \leq R_{max}$
- $\forall t, E^{out}_t \leq R_{max}$
- $\forall t, E^{out}_t \leq S_t$
- $\sum_{t'=t-23}^t E^{out}_{t'} \leq D_{max} \forall t \subset (T, t \geq 24)$

## Run the optimization model
The `optimize_year` function takes in the LBMP data from our new dataframe and returns the optimization results in a dataframe.

In [ ]:
results_df = optimize_year(df)

default domain for Param objects is 'Any'.  However, we will be
changing that default to 'Reals' in the future.  If you really intend
the domain of this Paramto be 'Any', you can suppress this warning by
explicitly specifying 'within=Any' to the Param constructor.
(deprecated in 5.6.9, will be removed in (or after) 6.0)
(called from /usr/local/lib/python3.10/dist-packages/pyomo/core/base/indexed_component.py:781)
position is deprecated.  Please use at()  (deprecated in 6.1, will be
removed in (or after) 7.0)
(called from <ipython-input-8-62e9b4bf6614>:25)


In [ ]:
results_df.head()

hour           timestamp  Ein      Eout   price  charge_state
0     0 2023-01-01 00:00:00  0.0  1.686547  195.90     12.000000
1     1 2023-01-01 01:00:00  0.0  0.000000  191.09     10.170683
2     2 2023-01-01 02:00:00  0.0  0.000000  187.95     10.170683
3     3 2023-01-01 03:00:00  0.0  0.000000  187.82     10.170683
4     4 2023-01-01 04:00:00  0.0  0.000000  187.74     10.170683

### Output results

In [ ]:
from google.colab import files

In [ ]:
results_df.to_csv('full_year_optimization_results2023.csv')

In [ ]:
files.download('full_year_optimization_results2023.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Analysis of results
In this exercise I've been asked to present the following:
- Summary values
    - Annual revenue
    - Annual charging costs
    - Annual discharged throughput
- Plots
    - Hourly dispatch and price for the most profitable week (assuming calendar week)
    - Total profit for each month

### Summary values
Revenue, costs, and profit still need to be calculated using energy in/out and the hourly price

In [ ]:
# Results
results_df['revenue'] = results_df.Eout * results_df.price
results_df['charge_cost'] = results_df.Ein * results_df.price
results_df['profit'] = results_df.revenue - results_df.charge_cost

In [ ]:
total_revenue = results_df.revenue.sum()
total_charge_cost = results_df.charge_cost.sum()
total_discharge = results_df.Eout.sum()
total_profit = results_df.profit.sum()

print('Annual revenue was €{:,.2f}'.format(total_revenue))
print('Annual charging cost was €{:,.2f}'.format(total_charge_cost))
print('Annual profit was €{:,.2f}'.format(total_profit))
print('Annual discharged throughput was {:,.2f} MWh'.format(total_discharge))

Annual revenue was €1,427,844.49
Annual charging cost was €822,421.42
Annual profit was €605,423.08
Annual discharged throughput was 8,091.35 MWh


### Figures

In [ ]:
results_df['week'] = results_df.timestamp.dt.isocalendar().week
results_df['month'] = results_df.timestamp.dt.month
results_df['hour_of_day'] = results_df.timestamp.dt.hour

The most profitable week was the 14th week of the year.

In [ ]:
profit_weekly = results_df.loc[results_df.timestamp >= '2020-01-01', :].groupby('week')['profit'].sum()


In [ ]:
print(profit_weekly)

week
1     11222.418010
2     13639.003663
3     22654.767862
4      8534.396942
5      8761.250265
6      8344.198368
7     12971.294719
8     11462.176448
9     10706.563460
10    19104.203495
11    22498.750370
12    15112.114784
13    20606.021054
14    13424.238400
15    13921.737249
16    15313.448483
17    13608.007842
18    10632.752753
19    11410.808923
20    16234.600157
21    10304.759914
22    10825.493899
23     4339.349714
24     9670.163765
25     8768.298633
26     5434.874063
27     6179.417799
28     7641.714221
29    13461.290200
30    13662.911028
31     5176.438196
32     9569.498815
33     8848.705031
34    14125.810106
35    11049.991707
36    11940.038080
37    10991.699194
38    10213.297137
39    13432.349581
40    15604.541320
41    10588.235249
42    13256.479586
43    14115.763665
44    18643.913999
45     9528.924536
46     8652.831189
47    10358.363091
48     9847.533774
49     7116.038227
50     7454.948874
51     7020.354955
52     7436.293799
Name: p

In [ ]:
results_df.loc[results_df.timestamp >= '2020-01-01', :].groupby('week')['profit'].sum().idxmax()

3

Including both the dispatch and hourly price in a single plot is difficult because their values have different scales. A dual y-axis plot can be difficult to read, so I've decided to show one plot on top of the other. The plot of price uses color to encode dispatch, which helps to make the whole thing easier to interprete.

In [ ]:
alt.renderers.enable('colab')

RendererRegistry.enable('colab')

In [ ]:
data = results_df.loc[(results_df.timestamp >= '2023-01-01') &
                      (results_df.week == 14), :].copy()
data.loc[:, 'dispatch'] = data.Ein - data.Eout
dispatch_data = pd.melt(data, id_vars='timestamp', value_vars=['Eout', 'Ein'], var_name='Dispatch')

color_scale = alt.Scale(
            domain=['Ein', 'Eout'],
            range=['#f99820', '#2081f9']
        )

dispatch = alt.Chart(dispatch_data).mark_line().encode(
    x='timestamp:T',
    y=alt.Y('value:Q', axis=alt.Axis(title='Electricity in/out (MWh)')),
    color=alt.Color('Dispatch:N', scale=color_scale)
).properties(
    height=400,
    width=800
)

price = alt.Chart(data).mark_circle().encode(
    x='timestamp:T',
    y=alt.Y('price:Q', axis=alt.Axis(title='Electricity Price (€)')),
    color=alt.Color('dispatch:Q', scale=alt.Scale(scheme='blueorange')),
    tooltip='dispatch:Q'
).properties(
    height=400,
    width=800
)

alt.vconcat(
    dispatch,
    price
)

/usr/local/lib/python3.10/dist-packages/altair/utils/core.py:384: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)


alt.VConcatChart(...)

In [ ]:
# Create Altair chart
alt.Chart(results_df).mark_line().encode(
    x='week:O',  # 'week' column as ordinal (categorical) for x-axis
    y='sum(profit):Q',  # 'profit' column as quantitative (numerical) for y-axis
    color=alt.condition(
        alt.datum['sum(profit)'] < 0,  # Condition for negative values
        alt.value('red'),  # Color for negative values
        alt.value('green')  # Default color for non-negative values
    )
).properties(
    height=300,
    width=800
)

alt.Chart(...)

In [ ]:
# Group by month and calculate the total profit for each month
profit_monthly = results_df.loc[results_df.timestamp >= '2020-01-01', :].groupby('month')['profit'].sum()

# Rename the columns for clarity
profit_monthly_df = profit_monthly.to_frame()

# Display the table
profit_monthly_df

profit
month              
1      59294.897802
2      43552.150649
3      80141.070813
4      61982.096733
5      51661.445521
6      33536.954415
7      44385.861042
8      43441.878590
9      48280.363203
10     60974.942869
11     50905.516369
12     27265.898586

In [ ]:
alt.Chart(results_df).mark_line().encode(
    x='month:O',
    y='sum(profit):Q'
).properties(
    height=300,
    width=500
)

alt.Chart(...)